### Dependencies

In [1]:
import numpy as np # Scientific computing 
import pandas as pd # Dataframe to organize content
import os # Creating folders
import pickle # Serializing module
import FATS # Feature extraction library
import sqlite3 # Database library
import urllib # Reading and saving webpages

/home/amanjot_bhullar/anaconda3/envs/py27/lib/python2.7/site-packages/statsmodels/compat/pandas.py:56: FutureWarning: The pandas.core.datetools module is deprecated and will be removed in a future version. Please use the pandas.tseries module instead.
  from pandas.core import datetools


### Scrape EB Stars from Astrouw then Store in Respective Directories
More specifically, this code will scrape a random set of ~2400 Eclipsing Binary Stars (~800 of EC, ESD, and ED each) from the Astrouw database (ftp://ftp.astrouw.edu.pl/ogle/ogle3/OIII-CVS/lmc/).

In [ ]:
# Read list file from web.
list_file_url = 'ftp://ftp.astrouw.edu.pl/ogle/ogle3/OIII-CVS/lmc/ecl/ident.dat'
list_file = pd.read_csv(list_file_url, sep="\s+", header=None, usecols=[0,3])

# This is an array of all EB stars on the astrouw website.
eb_stars = list_file.as_matrix()

# The EB stars are sorted using catagories EC, ESD, and EC.
eb_ec, eb_esd, eb_ed = np.array([]), np.array([]), np.array([])
for [name, cata] in eb_stars:
    if cata == 'EC':
        eb_ec = np.append(eb_ec, [name])
    if cata == 'ESD':
        eb_esd = np.append(eb_esd, [name])
    if cata == 'ED':
        eb_ed = np.append(eb_ed, [name])

# 800 random stars are selected from each catagory.
np.random.shuffle(eb_ec)        
np.random.shuffle(eb_esd)        
np.random.shuffle(eb_ed)
eb_ec = eb_ec[:800]
eb_esd = eb_esd[:800]
eb_ed = eb_ed[:800]

# Saving photometry data to corresponding folders.
directories = [('eb_ec', eb_ec), ('eb_esd', eb_esd), ('eb_ed', eb_ed)]
for (folder, cata) in directories: 
    for star in cata:
        url_I = 'ftp://ftp.astrouw.edu.pl/ogle/ogle3/OIII-CVS/lmc/ecl/phot/I/'+star+'.dat'
        url_V = 'ftp://ftp.astrouw.edu.pl/ogle/ogle3/OIII-CVS/lmc/ecl/phot/V/'+star+'.dat'
        try:
            urllib.urlretrieve(url_I, "Data/"+folder+"/I/"+star+".dat")
            urllib.urlretrieve(url_V, "Data/"+folder+"/V/"+star+".dat")
        except:
            pass
        # Clear the cache.
        urllib.urlcleanup()

print('Done')

### Extract Features from all Star Data
A detailed explanation of the features that are extracted is given on http://isadoranun.github.io/tsfeat/FeaturesDocumentation.html.  In the below code, features are extracted from each data-set and stored in a database.

In [ ]:
# A list of all star classes.
star_classes = os.listdir('Data/')

# Initializing database and cursor.
star_data_db = sqlite3.connect('star_data.db')
star_data_cursor = star_data_db.cursor()
    
# This loop will obtain the features for each star.
for star_class in star_classes:
    # Initializing table--(star type) and data type--(BLOB).
    star_data_cursor.execute("CREATE TABLE IF NOT EXISTS "+star_class+"(star_name BLOB, star_features BLOB)")
    
    # Find the stars that have both I-band and V-band data.
    stars_I = os.listdir('Data/'+star_class+'/I')
    stars_V = os.listdir('Data/'+star_class+'/V')
    overlapping_stars = [star for star in stars_I if star in stars_V]
    
    for star in overlapping_stars:
        print(star)
        # Reading Data for I-band.
        star_data_path_I = 'Data/'+star_class+'/I/'+star
        star_data_I = pd.read_csv(star_data_path_I, sep="\s+", names=["time", "magnitude", "error"])

        # Reading Data for V-band.
        star_data_path_V = 'Data/'+star_class+'/V/'+star
        star_data_V = pd.read_csv(star_data_path_V, sep="\s+", names=["time2", "magnitude2", "error2"])

        # Creating lists from pandas dataframe (these are the parameters used to compute the features).
        magnitude = star_data_I.magnitude.tolist()
        time = star_data_I.time.tolist()
        error = star_data_I.error.tolist()
        magnitude2 = star_data_V.magnitude2.tolist()

        #Extracting Features.
        parameters = np.array([magnitude, time, error])
        feature_space = FATS.FeatureSpace(Data=['magnitude','time', 'error'])
        features = feature_space.calculateFeature(parameters)
        features_array = features.result(method='array')
        # Custom feature:colour -- is also added to array.
        colour = np.mean(magnitude) - np.mean(magnitude2)
        features_array.append(colour)
        
        # Convert to float so that python3 can decode it.
        temp = [float(x) for x in features_array]

        # Serializing features so that it can be stored in database.
        features_pickled = pickle.dumps(temp, pickle.HIGHEST_PROTOCOL)

        # Storing star_data in database for future reference.
        star_data_cursor.execute("INSERT INTO "+star_class+"(star_name, star_features) VALUES (?,?)",
                                 (star, sqlite3.Binary(features_pickled)))
        star_data_db.commit()


print("Data stored.")

OGLE-LMC-LPV-02508.dat


/home/amanjot_bhullar/anaconda3/envs/py27/lib/python2.7/site-packages/scipy/optimize/_minimize.py:394: RuntimeWarning: Method nelder-mead cannot handle constraints nor bounds.
  RuntimeWarning)


OGLE-LMC-LPV-02758.dat
OGLE-LMC-LPV-01806.dat
OGLE-LMC-LPV-02123.dat
OGLE-LMC-LPV-02644.dat
OGLE-LMC-LPV-00701.dat
OGLE-LMC-LPV-01745.dat
OGLE-LMC-LPV-02513.dat
OGLE-LMC-LPV-01786.dat
OGLE-LMC-LPV-01347.dat
OGLE-LMC-LPV-00065.dat
OGLE-LMC-LPV-00677.dat
OGLE-LMC-LPV-01290.dat
OGLE-LMC-LPV-01087.dat
OGLE-LMC-LPV-02725.dat


OGLE-LMC-LPV-02051.dat
OGLE-LMC-LPV-00821.dat
OGLE-LMC-LPV-02692.dat
OGLE-LMC-LPV-01958.dat
OGLE-LMC-LPV-02393.dat
OGLE-LMC-LPV-02302.dat
OGLE-LMC-LPV-01731.dat
OGLE-LMC-LPV-01379.dat
OGLE-LMC-LPV-02928.dat
OGLE-LMC-LPV-01913.dat
OGLE-LMC-LPV-00435.dat
OGLE-LMC-LPV-02082.dat
OGLE-LMC-LPV-02419.dat
OGLE-LMC-LPV-02353.dat


OGLE-LMC-LPV-01809.dat
OGLE-LMC-LPV-02055.dat
OGLE-LMC-LPV-02815.dat
OGLE-LMC-LPV-00241.dat
OGLE-LMC-LPV-02184.dat
OGLE-LMC-LPV-01271.dat
OGLE-LMC-LPV-00010.dat
OGLE-LMC-LPV-02509.dat
OGLE-LMC-LPV-00066.dat
OGLE-LMC-LPV-01010.dat
OGLE-LMC-LPV-02838.dat
OGLE-LMC-LPV-02786.dat
OGLE-LMC-LPV-01487.dat
OGLE-LMC-LPV-02256.dat


...

OGLE-LMC-LPV-12735.dat
OGLE-LMC-LPV-09676.dat
OGLE-LMC-LPV-01845.dat
OGLE-LMC-LPV-08415.dat
OGLE-LMC-LPV-03050.dat
OGLE-LMC-LPV-11225.dat
OGLE-LMC-LPV-01802.dat
OGLE-LMC-LPV-00366.dat
OGLE-LMC-LPV-09969.dat
OGLE-LMC-LPV-02813.dat
OGLE-LMC-LPV-07059.dat
OGLE-LMC-LPV-03629.dat
OGLE-LMC-LPV-00756.dat
OGLE-LMC-LPV-12197.dat


OGLE-LMC-LPV-04693.dat
OGLE-LMC-LPV-03735.dat
OGLE-LMC-LPV-05732.dat
OGLE-LMC-LPV-04131.dat
OGLE-LMC-LPV-00341.dat
OGLE-LMC-LPV-04107.dat
OGLE-LMC-LPV-03338.dat
OGLE-LMC-LPV-05605.dat
OGLE-LMC-LPV-12204.dat
OGLE-LMC-LPV-03378.dat
OGLE-LMC-LPV-05524.dat
OGLE-LMC-LPV-04732.dat
OGLE-LMC-LPV-09311.dat
OGLE-LMC-LPV-08693.dat


OGLE-LMC-LPV-06044.dat
OGLE-LMC-LPV-11677.dat
OGLE-LMC-LPV-06636.dat
OGLE-LMC-LPV-10539.dat
OGLE-LMC-LPV-04493.dat
OGLE-LMC-LPV-12585.dat
OGLE-LMC-LPV-11558.dat
OGLE-LMC-LPV-11860.dat
OGLE-LMC-LPV-05596.dat
OGLE-LMC-LPV-09366.dat
OGLE-LMC-LPV-10788.dat
OGLE-LMC-LPV-10146.dat
OGLE-LMC-LPV-08298.dat
OGLE-LMC-LPV-05019.dat


OGLE-LMC-LPV-04625.dat
OGLE-LMC-LPV-00936.dat
OGLE-LMC-LPV-03681.dat
OGLE-LMC-LPV-08136.dat
OGLE-LMC-LPV-01387.dat
OGLE-LMC-LPV-04111.dat
OGLE-LMC-LPV-08083.dat
OGLE-LMC-LPV-09956.dat
OGLE-LMC-LPV-10231.dat
OGLE-LMC-LPV-03704.dat
OGLE-LMC-LPV-11186.dat
OGLE-LMC-LPV-02310.dat
OGLE-LMC-LPV-08178.dat
OGLE-LMC-LPV-08974.dat


OGLE-LMC-LPV-10128.dat
OGLE-LMC-LPV-06714.dat
OGLE-LMC-LPV-09381.dat
OGLE-LMC-LPV-06977.dat
Data stored.


### Retrieve Data from Database

In [2]:
# Initializing database and cursor
star_data_db = sqlite3.connect('star_data.db')
star_data_cursor = star_data_db.cursor()

# Retrieving star_data from database
star_data_cursor.execute('SELECT star_features FROM cep_1o')
for row in star_data_cursor.fetchall()[:5]:
    # BLOB field needs to be strinyfied with str() before loading with pickle
    data = pickle.loads(row[0])
    print(data)
    print(len(data))
    
# star_data_cursor.execute('SELECT star_data FROM astrouw_data')
# for row in star_data_cursor.fetchall()[:2]:
#     # BLOB field needs to be strinyfied with str() before loading with pickle
#     data = pickle.loads(str(row[0]))
#     print(data)
#     print(len(data))

# Close cursor and database    
star_data_cursor.close
star_data_db.close()

[0.070750000000000313, 1.0, 1.0, 0.49715909090909088, 6.7406541243280511, -0.043806403004365876, 2.2694431382836973, 0.0, 9.0043107648691549, 0.3059701492537466, 0.49253731343285323, 0.70895522388059995, 0.8358208955223867, 0.91791044776118669, 0.06473417480808609, 0.0033489840240962412, 0.005200197031870731, 0.0022605924121040146, 0.0, 2.016189043691746, 0.25089575391302033, 2.516418339258323, 0.0054049909438212071, 0.0012075724582677528, 0.00049352240324333481, 0.001368249653386237, 0.0, -0.19544797750107834, 0.42600745878354307, 1.5741767461125487, 0.0033693121459050512, 0.0015716141063143853, 0.00069698689429265027, 0.00017405917994078854, 0.0, 0.72741717243385307, 0.48184162806339942, -0.42631486369002547, -0.0075000000000038369, -1.715182367675642e-06, 0.14521917722966335, 15.297531249999999, 0.0030942424110401438, 0.046499999999996433, 0.15340909090909091, 0.16666666666666666, 0.0055884179221544136, 0.0087584561586980178, 1.938541306655778, 5.2655076356287659e-70, 0.233267531126

In [ ]:
star_data_db = sqlite3.connect('star_data.db')
star_data_cursor = star_data_db.cursor()
star_data_cursor.executescript('drop table if exists lpv_mira_agb_c;')